In [ ]:
import copy
import os

import numpy as np
import pandas as pd
from lmfit import  Model, Parameters

In [ ]:
def lq(x, alpha, beta):
    return (-alpha*x-beta*x**2)

# Fitting

In [ ]:
fname = os.path.join('tmp','rawdata.h5')
df = pd.read_hdf(fname, 'data_analyze')

In [ ]:
lqmodel = Model(lq, nanpolicy='propagate')
params = Parameters()
params.add('alpha', value=0.0002, min=0)
params.add('beta', value=0.0001, min=0, max=1e8)

In [ ]:
for name, group in df.groupby('article'):
    for energy, data in group.groupby('energy'):
        result = lqmodel.fit(params=params, 
                             data=np.log(data.sf), 
                             x=data.dose,
                             weights=np.fabs(1/(np.log(data.sf_err_up)-np.log(data.sf_err_down))))
        df.loc[(name,energy),'alfa_fit'] = result.values['alpha']
        df.loc[(name,energy),'alfa_fit_err'] = result.params['alpha'].stderr
        df.loc[(name,energy),'beta_fit'] = result.values['beta']
        df.loc[(name,energy),'beta_fit_err'] = result.params['beta'].stderr
        df.loc[(name,energy),'residuals']=np.abs(result.residual)
        df.loc[(name,energy),'residuals_limit']=np.abs(result.residual.std())
        df.loc[(name,energy),'covar_fit']=result.covar[1][0]
        df.loc[(name,energy),'fit_results']=copy.deepcopy(result)


In [ ]:
df.sort_index(inplace=True)

In [ ]:
df['diff_alfa']=df['alfa']-df['alfa_fit']
df['div_alfa']=df['alfa']/df['alfa_fit']
df['diff_beta']=df['beta']-df['beta_fit']
df['div_beta']=df['beta']/df['beta_fit']
df['alfa/beta']=df['alfa']/df['beta']
df['alfa(fit)/beta(fit)']=df['alfa_fit']/df['beta_fit']

In [ ]:
for name, group in df.groupby('article'):
        for energy, data in group.groupby('energy'):
            if energy==0:
                alfa_ref = data["alfa_fit"].max()
                beta_ref = data["beta_fit"].max()
                alfa_ref_art = data["alfa"].max()
                beta_ref_art = data["beta"].max()

                df.loc[(name,energy),'a(fit)/a_ref(fit)'] = 0.0
                df.loc[(name,energy),'b(fit)/b_ref(fit)'] = 0.0
                df.loc[(name,energy),'a/a_ref'] = 0.0
                df.loc[(name,energy),'b/b_ref'] = 0.0
            else :
                df.loc[(name,energy),'a(fit)/a_ref(fit)'] = (data["alfa_fit"])/alfa_ref 
                df.loc[(name,energy),'b(fit)/b_ref(fit)'] = (data["beta_fit"])/beta_ref 
                df.loc[(name,energy),'a/a_ref'] = (data["alfa"])/alfa_ref_art 
                df.loc[(name,energy),'b/b_ref'] = (data["beta"])/beta_ref_art 

# Save

In [ ]:
hdf_fname = os.path.join('tmp','fit.h5')
df[[item for item in df.columns if item != 'fit_results']].to_hdf(hdf_fname, 'data', format='table')